In [1]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from keras.models import Sequential
from keras.optimizers import Adam
from keras.callbacks import ModelCheckpoint
from keras.layers import Lambda, Conv2D, MaxPooling2D, Dropout, Dense, Flatten
import argparse
import os
import cv2
import matplotlib.image as mpimg

Using TensorFlow backend.
C:\ProgramData\Anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
C:\ProgramData\Anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
C:\ProgramData\Anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
C:\ProgramData\Anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py

In [2]:
IMAGE_HEIGHT, IMAGE_WIDTH, IMAGE_CHANNELS = 66, 200, 3
INPUT_SHAPE = (IMAGE_HEIGHT, IMAGE_WIDTH, IMAGE_CHANNELS)

In [75]:
def load_image(data_dir, image_file):
    return mpimg.imread(os.path.join(data_dir, image_file.strip()))

def crop(image):
    return image[60:-25, :, :]

def resize(image):
    return cv2.resize(image, (IMAGE_WIDTH, IMAGE_HEIGHT), cv2.INTER_AREA)

def rgb2yuv(image):
    return cv2.cvtColor(image, cv2.COLOR_RGB2YUV)

def preprocess(image):
    image = crop(image)
    image = resize(image)
    image = rgb2yuv(image)
    return image

def choose_image(data_dir, center, left, right, steering_angle):
    choice = np.random.choice(3)
    if choice == 0:
        return load_image(data_dir, left), steering_angle + 0.2
    elif choice == 1:
        return load_image(data_dir, right), steering_angle - 0.2
    return load_image(data_dir, center), steering_angle

def random_flip(image, steering_angle):
    if np.random.rand() < 0.5:
        image = cv2.flip(image, 1)
        steering_angle = -steering_angle
    return image, steering_angle

def random_translate(image, steering_angle, range_x, range_y):
    trans_x = range_x * (np.random.rand() - 0.5)
    trans_y = range_y * (np.random.rand() - 0.5)
    steering_angle += trans_x * 0.002
    trans_m = np.float32([[1, 0, trans_x], [0, 1, trans_y]])
    height, width = image.shape[:2]
    image = cv2.warpAffine(image, trans_m, (width, height))
    return image, steering_angle


def random_shadow(image):
    x1, y1 = IMAGE_WIDTH * np.random.rand(), 0
    x2, y2 = IMAGE_WIDTH * np.random.rand(), IMAGE_HEIGHT
    xm, ym = np.mgrid[0:IMAGE_HEIGHT, 0:IMAGE_WIDTH]

    mask = np.zeros_like(image[:, :, 1])
    mask[(ym - y1) * (x2 - x1) - (y2 - y1) * (xm - x1) > 0] = 1

    cond = mask == np.random.randint(2)
    s_ratio = np.random.uniform(low=0.2, high=0.5)

    hls = cv2.cvtColor(image, cv2.COLOR_RGB2HLS)
    hls[:, :, 1][cond] = hls[:, :, 1][cond] * s_ratio
    return cv2.cvtColor(hls, cv2.COLOR_HLS2RGB)

def random_brightness(image):
    hsv = cv2.cvtColor(image, cv2.COLOR_RGB2HSV)
    ratio = 1.0 + 0.4 * (np.random.rand() - 0.5)
    hsv[:,:,2] =  hsv[:,:,2] * ratio
    return cv2.cvtColor(hsv, cv2.COLOR_HSV2RGB)

def augument(data_dir, center, left, right, steering_angle, range_x=100, range_y=10):
    image, steering_angle = choose_image(data_dir, center, left, right, steering_angle)
    image, steering_angle = random_flip(image, steering_angle)
    image, steering_angle = random_translate(image, steering_angle, range_x, range_y)
    #image = random_shadow(image)
    #image = random_brightness(image)
    return image, steering_angle

def batch_generator(data_dir, image_paths, steering_angles, batch_size, is_training):
    images = np.empty([batch_size, IMAGE_HEIGHT, IMAGE_WIDTH, IMAGE_CHANNELS])
    steers = np.empty(batch_size)
    while True:
        i = 0
        for index in np.random.permutation(image_paths.shape[0]):
            center, left, right = image_paths[index]
            steering_angle = steering_angles[index]
            
            if is_training and np.random.rand() < 0.6:
                image, steering_angle = augument(data_dir, center, left, right, steering_angle)
                image = preprocess(image)
            else:
                image = load_image(data_dir, center)
                image = preprocess(image)
            images[i] = image
            steers[i] = steering_angle
            i += 1
            if i == batch_size:
                break
        yield images, steers

In [76]:
def load_data(args):
    data_df = pd.read_csv(os.path.join(os.getcwd(), args['data_dir'], 'driving_log.csv'), names=['center', 'left', 'right', 'steering', 'throttle', 'reverse', 'speed'])

    X = data_df[['center', 'left', 'right']].values
    y = data_df['steering'].values
    X_train, X_valid, y_train, y_valid = train_test_split(X, y, test_size=args['test_size'], random_state=0)

    return X_train, X_valid, y_train, y_valid

In [77]:
def build_model(args):
    model = Sequential()
    model.add(Lambda(lambda x: x/127.5-1.0, input_shape=INPUT_SHAPE))
    model.add(Conv2D(24, 5, 5, activation='elu', subsample=(2, 2)))
    model.add(Conv2D(36, 5, 5, activation='elu', subsample=(2, 2)))
    model.add(Conv2D(48, 5, 5, activation='elu', subsample=(2, 2)))
    model.add(Conv2D(64, 3, 3, activation='elu'))
    model.add(Conv2D(64, 3, 3, activation='elu'))
    model.add(Dropout(args['keep_prob']))
    model.add(Flatten())
    model.add(Dense(100, activation='elu'))
    model.add(Dense(50, activation='elu'))
    model.add(Dense(10, activation='elu'))
    model.add(Dense(1))
    model.summary()

    return model

In [94]:
def train_model(model, args, X_train, X_valid, y_train, y_valid):
    checkpoint = ModelCheckpoint('model2-{epoch:03d}.h5',
                                 monitor='val_loss',
                                 verbose=0,
                                 save_best_only=args['save_best_only'],
                                 mode='auto')

    model.compile(loss='mean_squared_error', optimizer=Adam(lr=args['learning_rate']))

    model.fit_generator(batch_generator(args['data_dir'], X_train, y_train, args['batch_size'], True),
                        args['samples_per_epoch'],
                        args['nb_epoch'],
                        max_q_size=1,
                        validation_data=batch_generator(args['data_dir'], X_valid, y_valid, args['batch_size'], False),
                        nb_val_samples=len(X_valid),
                        callbacks=[checkpoint],
                        verbose=1)

In [95]:
def s2b(s):
    """
    Converts a string to boolean value
    """
    s = s.lower()
    return s == 'true' or s == 'yes' or s == 'y' or s == '1'

In [96]:
args = {'data_dir' : 'data2',
       'test_size' : 0.2,
       'keep_prob' : 0.5,
       'nb_epoch' : 10,
       'samples_per_epoch' : 20000,
       'batch_size' : 40,
       'save_best_only' : 'true',
       'learning_rate' : 1.0e-4}

In [97]:
print('-' * 30)
print('Parameters')
print('-' * 30)
for key, value in zip(args.keys(), args.values()):
    print('{:<20} := {}'.format(key, value))
print('-' * 30)

data = load_data(args)

model = build_model(args)

train_model(model, args, *data)

------------------------------
Parameters
------------------------------
data_dir             := data2
test_size            := 0.2
keep_prob            := 0.5
nb_epoch             := 10
samples_per_epoch    := 20000
batch_size           := 40
save_best_only       := true
learning_rate        := 0.0001
------------------------------
Model: "sequential_16"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
lambda_16 (Lambda)           (None, 66, 200, 3)        0         
_________________________________________________________________
conv2d_76 (Conv2D)           (None, 31, 98, 24)        1824      
_________________________________________________________________
conv2d_77 (Conv2D)           (None, 14, 47, 36)        21636     
_________________________________________________________________
conv2d_78 (Conv2D)           (None, 5, 22, 48)         43248     
_________________________________________________

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:4: UserWarning: Update your `Conv2D` call to the Keras 2 API: `Conv2D(24, (5, 5), activation="elu", strides=(2, 2))`
  after removing the cwd from sys.path.
C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:5: UserWarning: Update your `Conv2D` call to the Keras 2 API: `Conv2D(36, (5, 5), activation="elu", strides=(2, 2))`
  """
C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:6: UserWarning: Update your `Conv2D` call to the Keras 2 API: `Conv2D(48, (5, 5), activation="elu", strides=(2, 2))`
  
C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:7: UserWarning: Update your `Conv2D` call to the Keras 2 API: `Conv2D(64, (3, 3), activation="elu")`
  import sys
C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Update your `Conv2D` call to the Keras 2 API: `Conv2D(64, (3, 3), activation="elu")`
  
C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_laun

Epoch 1/10
20000/20000 [==============================] - 934s 47ms/step - loss: 0.1023 - val_loss: 0.0904 0.1623 - ETA: 13:52 - loss: 0.1352 - ETA: 9:55 - loss: 0.1162 - ETA: 9:52 - loss: 0.1160 - ETA: 9:24 - loss: 0.1147 - ETA: 8:54 - loss: 0.1139 - ETA: 8:09 - loss: 0.1125 - ETA: 7:50 - loss: 0.1119 - ETA: 7:20 - loss: 0.1110 - ETA: 4:51 - loss: 0.1074 - ETA: 4:35 - loss: 0.1071 - ETA: 3:27 - loss: 0.1057 - ETA: 2:57 - loss: 0.1051 - ETA: 1:53 - loss: 0.1040 - ETA: 1:14 - loss: 0.1033 - ETA: 56s - loss: 0.1031 - ETA: 45s - loss: 0.1030
Epoch 2/10
20000/20000 [==============================] - 915s 46ms/step - loss: 0.0833 - val_loss: 0.0853.0877 - ETA: 12:47 - loss: 0.0877 - ETA: 12:12 - loss: 0.0878 - ETA: 12:03 - loss: 0.0876 - ETA: 11:07 - loss: 0.0872 - ETA: 10:26 - loss: 0.0872 - ETA: 10:07 - loss: 0.0865 - ETA: 10:05 - loss: 0.0865 - ETA: 10:04 - loss: 0.0864 - ETA: 10:01 - loss: 0.0863 - ETA: 7:54 - loss: 0.0856 - ETA: 7:44 - loss: 0.0855 - ETA: 7:32 - loss: 0.0854 - ETA: 7:0

In [98]:
import argparse
import base64
from datetime import datetime
import os
import shutil
import numpy as np
import socketio
import eventlet
import eventlet.wsgi
from PIL import Image
from flask import Flask
from io import BytesIO

from keras.models import load_model

sio = socketio.Server()

app = Flask(__name__)

model = None
prev_image_array = None

MAX_SPEED = 25
MIN_SPEED = 10

speed_limit = MAX_SPEED

@sio.on('telemetry')
def telemetry(sid, data):
    if data:
        steering_angle = float(data["steering_angle"])

        throttle = float(data["throttle"])

        speed = float(data["speed"])

        image = Image.open(BytesIO(base64.b64decode(data["image"])))
        try:
            image = np.asarray(image)
            image = preprocess(image)
            image = np.array([image])

            steering_angle = float(model.predict(image, batch_size=1))

            global speed_limit
            if speed > speed_limit:
                speed_limit = MIN_SPEED
            else:
                speed_limit = MAX_SPEED
            throttle = 1.0 - steering_angle**2 - (speed/speed_limit)**2

            print('{} {} {}'.format(steering_angle, throttle, speed))
            send_control(steering_angle, throttle)
        except Exception as e:
            print(e)

        if args['image_folder'] != '':
            timestamp = datetime.utcnow().strftime('%Y_%m_%d_%H_%M_%S_%f')[:-3]
            image_filename = os.path.join(args['image_folder'], timestamp)
            image.save('{}.jpg'.format(image_filename))
    else:
        
        sio.emit('manual', data={}, skip_sid=True)


@sio.on('connect')
def connect(sid, environ):
    print("connect ", sid)
    send_control(0, 0)


def send_control(steering_angle, throttle):
    sio.emit(
        "steer",
        data={
            'steering_angle': steering_angle.__str__(),
            'throttle': throttle.__str__()
        },
        skip_sid=True)

In [ ]:
args = {'model' : 'model2-009.h5',
       'image_folder' : 'run'}


model = load_model(args['model'])

if args['image_folder'] != '':
    print("Creating image folder at {}".format(args['image_folder']))
    if not os.path.exists(args['image_folder']):
        os.makedirs(args['image_folder'])
    else:
        shutil.rmtree(args['image_folder'])
        os.makedirs(args['image_folder'])
    print("RECORDING THIS RUN ...")
else:
    print("NOT RECORDING THIS RUN ...")

app = socketio.Middleware(sio, app)

eventlet.wsgi.server(eventlet.listen(('', 4567)), app)

Creating image folder at run
RECORDING THIS RUN ...
connect  861b07ae10af4ea2a15cdec922be4049


(12720) wsgi starting up on http://0.0.0.0:4567
(12720) accepted ('127.0.0.1', 50419)


-0.046266108751297 0.9978594471810132 0.0
-0.046266108751297 0.9978594471810132 0.0
-0.046266108751297 0.9978594471810132 0.0
-0.04589426517486572 0.9978937164240591 0.0
-0.04589426517486572 0.9978937164240591 0.0
-0.042789068073034286 0.9981101132534412 0.192
-0.042789068073034286 0.9979576840534412 0.3635
-0.04714559018611908 0.9971023329260025 0.6495
-0.04398734122514725 0.9973901534119425 0.6495
-0.06190042942762375 0.9947599860526758 0.9382
-0.06190042942762375 0.9942467419406759 1.0959
-0.058805614709854126 0.9946203047825962 1.0959
-0.058805614709854126 0.9936444460945962 1.3457
-0.05715251713991165 0.9927736566005722 1.5732
-0.06185600906610489 0.992213900958414 1.5732

Exception in thread Thread-43549:
Traceback (most recent call last):
  File "C:\ProgramData\Anaconda3\lib\threading.py", line 917, in _bootstrap_inner
    self.run()
  File "C:\ProgramData\Anaconda3\lib\threading.py", line 865, in run
    self._target(*self._args, **self._kwargs)
  File "C:\ProgramData\Anaconda3\lib\site-packages\socketio\server.py", line 599, in _handle_event_internal
    r = server._trigger_event(data[0], namespace, sid, *data[1:])
  File "C:\ProgramData\Anaconda3\lib\site-packages\socketio\server.py", line 628, in _trigger_event
    return self.handlers[namespace][event](*args)
  File "<ipython-input-98-f71607994b46>", line 60, in telemetry
    image.save('{}.jpg'.format(image_filename))
AttributeError: 'numpy.ndarray' object has no attribute 'save'

Exception in thread Thread-43550:
Traceback (most recent call last):
  File "C:\ProgramData\Anaconda3\lib\threading.py", line 917, in _bootstrap_inner
    self.run()
  File "C:\ProgramData\Anaconda3\lib\threading.py", l


-0.05732002854347229 0.9913737279277756 1.827
-0.05732002854347229 0.9898804161037755 2.0667
-0.07245578616857529 0.9879161608266938 2.0667
-0.07245578616857529 0.9862868950346938 2.2999
-0.06436014175415039 0.9873945081373857 2.2999
-0.08789800107479095 0.982128617231056 2.5181
-0.1096603199839592 0.9758041118210158 2.758
-0.07742542773485184 0.9796800857960752 2.9922
-0.07742542773485184 0.9773880306760753 3.2227
-0.057439904659986496 0.9776345709526517 3.452
-0.08953487873077393 0.9729174190906656 3.452
-0.08069305866956711 0.9718101905865498 3.6809
-0.08069305866956711 0.9690364278985498 3.9093

...

Exception in thread Thread-59491:
Traceback (most recent call last):
  File "C:\ProgramData\Anaconda3\lib\threading.py", line 917, in _bootstrap_inner
    self.run()
  File "C:\ProgramData\Anaconda3\lib\threading.py", line 865, in run
    self._target(*self._args, **self._kwargs)
  File "C:\ProgramData\Anaconda3\lib\site-packages\socketio\server.py", line 599, in _handle_event_internal
    r = server._trigger_event(data[0], namespace, sid, *data[1:])
  File "C:\ProgramData\Anaconda3\lib\site-packages\socketio\server.py", line 628, in _trigger_event
    return self.handlers[namespace][event](*args)
  File "<ipython-input-98-f71607994b46>", line 60, in telemetry
    image.save('{}.jpg'.format(image_filename))
AttributeError: 'numpy.ndarray' object has no attribute 'save'

Exception in thread Thread-59492:
Traceback (most recent call last):
  File "C:\ProgramData\Anaconda3\lib\threading.py", line 917, in _bootstrap_inner
    self.run()
  File "C:\ProgramData\Anaconda3\lib\threading.py", l

-0.04799111187458038 -8.115818846418959 30.1886
-0.04799111187458038 -8.115818846418959 30.1886
-0.04796494543552399 -8.093550764890635 30.1517
-0.09463988244533539 -7.914943511449268 29.8429
-0.09463988244533539 -7.916972944249267 29.8463
-0.12583374977111816 -7.70925050418146 29.4846
-0.0628441572189331 -7.697365759696558 29.4846
-0.09285134822130203 -7.488773057766513 29.1207
-0.06575879454612732 -7.274894958660162 28.7586
-0.06575879454612732 -7.274894958660162 28.7586
-0.11705628782510757 -7.079302174519395 28.4
-0.08640269935131073 -6.870498318555193 28.0411
-0.07519891858100891 -6.670357867755751 27.6852
-0.07519891858100891 -6.473850717355754 27.328

Exception in thread Thread-65513:
Traceback (most recent call last):
  File "C:\ProgramData\Anaconda3\lib\threading.py", line 917, in _bootstrap_inner
    self.run()
  File "C:\ProgramData\Anaconda3\lib\threading.py", line 865, in run
    self._target(*self._args, **self._kwargs)
  File "C:\ProgramData\Anaconda3\lib\site-packages\socketio\server.py", line 599, in _handle_event_internal
    r = server._trigger_event(data[0], namespace, sid, *data[1:])
  File "C:\ProgramData\Anaconda3\lib\site-packages\socketio\server.py", line 628, in _trigger_event
    return self.handlers[namespace][event](*args)
  File "<ipython-input-98-f71607994b46>", line 60, in telemetry
    image.save('{}.jpg'.format(image_filename))
AttributeError: 'numpy.ndarray' object has no attribute 'save'

Exception in thread Thread-65514:
Traceback (most recent call last):
  File "C:\ProgramData\Anaconda3\lib\threading.py", line 917, in _bootstrap_inner
    self.run()
  File "C:\ProgramData\Anaconda3\lib\threading.py", l


-0.0783614069223404 -6.474336350094849 27.328


Exception in thread Thread-65526:
Traceback (most recent call last):
  File "C:\ProgramData\Anaconda3\lib\threading.py", line 917, in _bootstrap_inner
    self.run()
  File "C:\ProgramData\Anaconda3\lib\threading.py", line 865, in run
    self._target(*self._args, **self._kwargs)
  File "C:\ProgramData\Anaconda3\lib\site-packages\socketio\server.py", line 599, in _handle_event_internal
    r = server._trigger_event(data[0], namespace, sid, *data[1:])
  File "C:\ProgramData\Anaconda3\lib\site-packages\socketio\server.py", line 628, in _trigger_event
    return self.handlers[namespace][event](*args)
  File "<ipython-input-98-f71607994b46>", line 60, in telemetry
    image.save('{}.jpg'.format(image_filename))
AttributeError: 'numpy.ndarray' object has no attribute 'save'

Exception in thread Thread-65527:
Traceback (most recent call last):
  File "C:\ProgramData\Anaconda3\lib\threading.py", line 917, in _bootstrap_inner
    self.run()
  File "C:\ProgramData\Anaconda3\lib\threading.py", l